In [1]:
import math
from math import degrees

def calculate_angle(ax, ay, bx, by, cx, cy):
    alpha0 = math.atan2(ay-by,ax-bx)*180 / math.pi
    alpha1 = math.atan2(cy-by,cx-bx)*180 / math.pi
    if alpha0 * alpha1 >= 0:
        angle = abs(alpha0 - alpha1)
    else:
        angle = abs(alpha0) + abs(alpha1)
        if angle > 180:
            angle = 360 - angle
            
    print("0 = ", alpha0, ", 1 = ", alpha1, ", angle = ", angle)
    return angle


In [ ]:
#importing the libraries
import numpy as np #for mathematical calculations
import cv2 #for face detection and other image operations
import dlib #for detection of facial landmarks ex:nose,jawline,eyes
from sklearn.cluster import KMeans #for clustering

#load the image
#imagepath = "test.jfif"
imagepath = "face match/test.jfif"
#haarcascade for detecting faces
# link = https://github.com/opencv/opencv/tree/master/data/haarcascades
face_cascade_path = "face match/haarcascade_frontalface_default.xml"
#.dat file for detecting facial landmarks
#download file path = http://dlib.net/files/shape_predictor_68_face_landmarks.dat.bz2
predictor_path = "face match/shape_predictor_68_face_landmarks.dat"

#create the haar cascade for detecting face and smile
faceCascade = cv2.CascadeClassifier(face_cascade_path)

#create the landmark predictor
predictor = dlib.shape_predictor(predictor_path)

#read the image
image = cv2.imread(imagepath)
img_src = "https://cdn.style-map.com/post/photo/normal/492873.jpg"
#cap = cv2.VideoCapture(img_src)
cap = cv2.VideoCapture(imagepath)
if( cap.isOpened() ) :
    ret,image = cap.read()

    zoom = 500/image.shape[1]
    image = cv2.resize(image, (500, int(image.shape[0]*zoom))) 
    print(image.shape)
    #making another copy
    original = image.copy()

    #convert the image to grayscale
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)

    #apply a Gaussian blur with a 3 x 3 kernel to help remove high frequency noise
    gauss = cv2.GaussianBlur(gray,(3,3), 0)

    #Detect faces in the image
    faces = faceCascade.detectMultiScale(
        gauss,
        scaleFactor=1.05,
        minNeighbors=5,
        minSize=(100,100),
        flags=cv2.CASCADE_SCALE_IMAGE
        )
    #Detect faces in the image
    print("found {0} faces!".format(len(faces)) )
    if len(faces) == 1:
        for (x,y,w,h) in faces:
            #draw a rectangle around the faces
            cv2.rectangle(image, (x,y), (x+w,y+h), (0,255,0), 2)
            #converting the opencv rectangle coordinates to Dlib rectangle
            dlib_rect = dlib.rectangle(int(x), int(y), int(x+w), int(y+h))
            #detecting landmarks
            detected_landmarks = predictor(image, dlib_rect).parts()
            #converting to np matrix
            landmarks = np.matrix([[p.x,p.y] for p in detected_landmarks])
            #landmarks array contains indices of landmarks.

        #making another copy  for showing final results
        results = original.copy()

        for (x,y,w,h) in faces:
            #draw a rectangle around the faces
            cv2.rectangle(results, (x,y), (x+w,y+h), (0,255,0), 2)
            #making temporary copy
            temp = original.copy()
            #getting area of interest from image i.e., forehead (25% of face)
            forehead = temp[y:y+int(0.25*h), x:x+w]
            rows,cols, bands = forehead.shape
            X = forehead.reshape(rows*cols,bands)
            """
            Applying kmeans clustering algorithm for forehead with 2 clusters 
            this clustering differentiates between hair and skin (thats why 2 clusters)
            """
            #kmeans
            kmeans = KMeans(n_clusters=2,init='k-means++',max_iter=300,n_init=10, random_state=0)
            y_kmeans = kmeans.fit_predict(X)
            print(y_kmeans)
            for i in range(0,rows):
                for j in range(0,cols):
                    if y_kmeans[i*cols+j]==True:
                        forehead[i][j]=[255,255,255]
                    if y_kmeans[i*cols+j]==False:
                        forehead[i][j]=[0,0,0]
            #Steps to get the length of forehead
            #1.get midpoint of the forehead
            #2.travel left side and right side
            #the idea here is to detect the corners of forehead which is the hair.
            #3.Consider the point which has change in pixel value (which is hair)
            forehead_mid = [int(cols/2), int(rows/2) ] #midpoint of forehead
            lef=0 
            count = 0
            tmp = 0
            #gets the value of forehead point
            pixel_value = forehead[forehead_mid[1],forehead_mid[0] ]
            for i in range(0,cols):
                #enters if when change in pixel color is detected
                if forehead_mid[0]-i <= 0:
                    break
                if forehead[forehead_mid[1],forehead_mid[0]-i].all()!=pixel_value.all():
                    lef=forehead_mid[0]-i
                    if(tmp == 0 or tmp != lef + 1):
                        tmp = lef
                        count -= 1
                    
                    count+=1
                    if count == 5:
                        break;
            left = [lef,forehead_mid[1]]
            print("left: ", left)
            rig=forehead_mid[0]
            count = 0
            tmp = 0
            for i in range(0,cols):
                #print("forehead[forehead_mid[1],forehead_mid[0]+i].all(): ", forehead[forehead_mid[1],forehead_mid[0]+i].all())
                #enters if when change in pixel color is detected
                if forehead_mid[0]+i >= cols:
                    break
                if forehead[forehead_mid[1],forehead_mid[0]+i].all()!=pixel_value.all():
                    rig = forehead_mid[0]+i
                    if(tmp == 0 or tmp != rig - 1):
                        tmp = rig
                        count -= 1
                    
                    count+=1
                    
                    if count == 5:
                        break;
            right = [rig,forehead_mid[1]]
            print("right: ", right)

        #drawing line1 on forehead with circles
        #specific landmarks are used. 
        
        begin_point = (x+left[0], y+left[1])
        end_point = (x+right[0], y+right[1])
        
        line1 = np.subtract(end_point,begin_point)[0]
        cv2.line(results, tuple(begin_point), tuple(end_point), color=(0,255,0), thickness = 2)
        cv2.putText(results,' Line 1',tuple(begin_point),fontFace=cv2.FONT_HERSHEY_SIMPLEX,fontScale=1,color=(0,255,0), thickness=2)
        cv2.circle(results, tuple(begin_point), 5, color=(255,0,0), thickness=-1)    
        cv2.circle(results, tuple(end_point), 5, color=(255,0,0), thickness=-1)        

        #drawing line 2 with circles
        linepointleft = (landmarks[1,0],landmarks[1,1])
        linepointright = (landmarks[15,0],landmarks[15,1])
        line2 = np.subtract(linepointright,linepointleft)[0]
        cv2.line(results, linepointleft,linepointright,color=(0,255,0), thickness = 2)
        cv2.putText(results,' Line 2',linepointleft,fontFace=cv2.FONT_HERSHEY_SIMPLEX,fontScale=1,color=(0,255,0), thickness=2)
        cv2.circle(results, linepointleft, 5, color=(255,0,0), thickness=-1)    
        cv2.circle(results, linepointright, 5, color=(255,0,0), thickness=-1)    

        #drawing line 3 with circles
        linepointleft = (landmarks[3,0],landmarks[3,1])
        linepointright = (landmarks[13,0],landmarks[13,1])
        line3 = np.subtract(linepointright,linepointleft)[0]
        cv2.line(results, linepointleft,linepointright,color=(0,255,0), thickness = 2)
        cv2.putText(results,' Line 3',linepointleft,fontFace=cv2.FONT_HERSHEY_SIMPLEX,fontScale=1,color=(0,255,0), thickness=2)
        cv2.circle(results, linepointleft, 5, color=(255,0,0), thickness=-1)    
        cv2.circle(results, linepointright, 5, color=(255,0,0), thickness=-1)    

        #drawing line 4 with circles
        linepointbottom = (landmarks[8,0],landmarks[8,1])
        linepointtop = (landmarks[8,0],y)
        line4 = np.subtract(linepointbottom,linepointtop)[1]
        cv2.line(results,linepointtop,linepointbottom,color=(0,255,0), thickness = 2)
        cv2.putText(results,' Line 4',linepointbottom,fontFace=cv2.FONT_HERSHEY_SIMPLEX,fontScale=1,color=(0,255,0), thickness=2)
        cv2.circle(results, linepointtop, 5, color=(255,0,0), thickness=-1)    
        cv2.circle(results, linepointbottom, 5, color=(255,0,0), thickness=-1)    
        print(line1,line2,line3,line4)
        
        zoom = 200/line4
        line1 *= zoom
        line2 *= zoom
        line3 *= zoom
        line4 = 200
        
        print("after")
        print(line1,line2,line3,line4)
        
        #for i in range(1, 16):
        #    cv2.circle(results, (landmarks[i,0],landmarks[i,1]), 5, color=(255,0,255), thickness=-1)    
        
        
        ax, ay = landmarks[6,0],landmarks[6,1]
        bx, by = landmarks[8,0],landmarks[8,1]
        cx, cy = landmarks[10,0],landmarks[10,1]
        angle = calculate_angle(ax, ay, bx, by, cx, cy)
        
        dx, dy = landmarks[7,0],landmarks[7,1]
        ex, ey = landmarks[9,0],landmarks[9,1]
        angle2 = calculate_angle(dx, dy, bx, by, ex, ey)
        
        if line1 < line2 - 40 or line1 > line2 + 40:
            print("none")
            
        #result = [0, 0, 0, 0]
        result = ""
        if line1 > line2 and line1 > line3:
            #result[0] = 1
            result += "1"
        elif line2 > line1 and line2 > line3:
            #result[0] = 2
            result += "2"
        else:
            #result[0] = 3
            result += "3"
        
        if line4 > line2 + 30:
            #result[1] = 1
            result += "1"
        else:
            #result[1] = 2
            result += "2"
        
        if line1 < line3 + 10 and line1 > line3 - 10:
            #result[2] = 1
            result += "1"
        elif line1 > line3 + 10:
            #result[2] = 2
            result += "2"
        else:
            #result[2] = 3
            result += "3"
            
        if angle <= 130:
            #result[3] = 1
            result += "1"
        else:
            if angle2 > 170:
                #result[3] = 2
                result += "2"
            else:
                #result[3] = 3
                result += "3"
        
        rectangular = [1111, 1112, 1113, 1121, 1122, 1123, 1211, 2111, 2112, 2113, 2121, 2122, 2123, 2131, 2132, 2133, 3111, 3112, 3113, 3131, 3132, 3133, 3211]
        round = [2213, 2223]
        square = [1212, 1213, 1223, 2212, 2231, 2232, 2233, 3212, 3213, 3231, 3232, 3233]
        oval = [2211, 2221, 2222]
        heart = [1221, 1222]
        
        print(result)
        for compare in rectangular:
            if int(result) == compare:
                print("rectangular")
                break
        for compare in round:
            if int(result) == compare:
                print("round")
                break
        for compare in square:
            if int(result) == compare:
                print("square")
                break
        for compare in oval:
            if int(result) == compare:
                print("oval")
                break
        for compare in heart:
            if int(result) == compare:
                print("heart")
                break
        
        
        output = np.concatenate((original,results), axis=1)
        cv2.imshow('output',output)
        cv2.waitKey(0)
        cv2.destroyAllWindows()

    

(503, 500, 3)
found 1 faces!
[0 0 0 ... 1 1 1]
left:  [34, 28]
right:  [189, 28]
155 161 146 224
after
138.39285714285714 143.75 130.35714285714286 200
0 =  -154.72227776444703 , 1 =  -31.218402764346372 , angle =  123.50387500010066
0 =  -171.02737338510363 , 1 =  -15.524110996754256 , angle =  155.50326238834938
2111
rectangular


In [3]:
def get_face_shape(img_src):
    print("img_src:")
    print(img_src)
    #haarcascade for detecting faces
    # link = https://github.com/opencv/opencv/tree/master/data/haarcascades
    face_cascade_path = "face match/haarcascade_frontalface_default.xml"
    #.dat file for detecting facial landmarks
    #download file path = http://dlib.net/files/shape_predictor_68_face_landmarks.dat.bz2
    predictor_path = "face match/shape_predictor_68_face_landmarks.dat"

    #create the haar cascade for detecting face and smile
    faceCascade = cv2.CascadeClassifier(face_cascade_path)

    #create the landmark predictor
    predictor = dlib.shape_predictor(predictor_path)

    #read the image
    cap = cv2.VideoCapture(img_src)
    if( cap.isOpened() ) :
        ret,image = cap.read()

        zoom = 500/image.shape[1]
        image = cv2.resize(image, (500, int(image.shape[0]*zoom))) 
        #making another copy
        original = image.copy()

        #convert the image to grayscale
        gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)

        #apply a Gaussian blur with a 3 x 3 kernel to help remove high frequency noise
        gauss = cv2.GaussianBlur(gray,(3,3), 0)

        #Detect faces in the image
        faces = faceCascade.detectMultiScale(
            gauss,
            scaleFactor=1.05,
            minNeighbors=5,
            minSize=(100,100),
            flags=cv2.CASCADE_SCALE_IMAGE
            )
        #Detect faces in the image
        print("found {0} faces!".format(len(faces)) )
        if len(faces) != 1:
            return 'none'
        if len(faces) == 1:
            for (x,y,w,h) in faces:
                #draw a rectangle around the faces
                cv2.rectangle(image, (x,y), (x+w,y+h), (0,255,0), 2)
                #converting the opencv rectangle coordinates to Dlib rectangle
                dlib_rect = dlib.rectangle(int(x), int(y), int(x+w), int(y+h))
                #detecting landmarks
                detected_landmarks = predictor(image, dlib_rect).parts()
                #converting to np matrix
                landmarks = np.matrix([[p.x,p.y] for p in detected_landmarks])
                #landmarks array contains indices of landmarks.

            #making another copy  for showing final results
            results = original.copy()

            
        for (x,y,w,h) in faces:
            #making temporary copy
            temp = original.copy()
            #getting area of interest from image i.e., forehead (25% of face)
            forehead = temp[y:y+int(0.25*h), x:x+w]
            rows,cols, bands = forehead.shape
            X = forehead.reshape(rows*cols,bands)
            """
            Applying kmeans clustering algorithm for forehead with 2 clusters 
            this clustering differentiates between hair and skin (thats why 2 clusters)
            """
            #kmeans
            kmeans = KMeans(n_clusters=2,init='k-means++',max_iter=300,n_init=10, random_state=0)
            y_kmeans = kmeans.fit_predict(X)
            for i in range(0,rows):
                for j in range(0,cols):
                    if y_kmeans[i*cols+j]==True:
                        forehead[i][j]=[255,255,255]
                    if y_kmeans[i*cols+j]==False:
                        forehead[i][j]=[0,0,0]
            #Steps to get the length of forehead
            #1.get midpoint of the forehead
            #2.travel left side and right side
            #the idea here is to detect the corners of forehead which is the hair.
            #3.Consider the point which has change in pixel value (which is hair)
            forehead_mid = [int(cols/2), int(rows/2) ] #midpoint of forehead
            lef=0 
            count = 0
            tmp = 0
            #gets the value of forehead point
            pixel_value = forehead[forehead_mid[1],forehead_mid[0] ]
            for i in range(0,cols):
                #enters if when change in pixel color is detected
                if forehead_mid[0]-i <= 0:
                    break
                if forehead[forehead_mid[1],forehead_mid[0]-i].all()!=pixel_value.all():
                    lef=forehead_mid[0]-i
                    if(tmp == 0 or tmp != lef + 1):
                        tmp = lef
                        count -= 1
                    
                    count+=1
                    if count == 5:
                        break;
            left = [lef,forehead_mid[1]]
            print("left: ", left)
            rig=forehead_mid[0]
            count = 0
            tmp = 0
            for i in range(0,cols):
                #enters if when change in pixel color is detected
                if forehead_mid[0]+i >= cols:
                    break
                if forehead[forehead_mid[1],forehead_mid[0]+i].all()!=pixel_value.all():
                    rig = forehead_mid[0]+i
                    if(tmp == 0 or tmp != rig - 1):
                        tmp = rig
                        count -= 1
                    
                    count+=1
                    if count == 5:
                        break;
            right = [rig,forehead_mid[1]]
            print("right: ", right)

            #specific landmarks are used. 

            begin_point = (x+left[0], y+left[1])
            end_point = (x+right[0], y+right[1])

            line1 = np.subtract(end_point,begin_point)[0]
            
            linepointleft = (landmarks[1,0],landmarks[1,1])
            linepointright = (landmarks[15,0],landmarks[15,1])
            line2 = np.subtract(linepointright,linepointleft)[0]
            
            linepointleft = (landmarks[3,0],landmarks[3,1])
            linepointright = (landmarks[13,0],landmarks[13,1])
            line3 = np.subtract(linepointright,linepointleft)[0]
            
            linepointbottom = (landmarks[8,0],landmarks[8,1])
            linepointtop = (landmarks[8,0],y)
            line4 = np.subtract(linepointbottom,linepointtop)[1]
            
            zoom = 200/line4
            line1 *= zoom
            line2 *= zoom
            line3 *= zoom
            line4 = 200
            
            print(line1,line2,line3,line4)
            
            ax, ay = landmarks[6,0],landmarks[6,1]
            bx, by = landmarks[8,0],landmarks[8,1]
            cx, cy = landmarks[10,0],landmarks[10,1]
            angle = calculate_angle(ax, ay, bx, by, cx, cy)

            dx, dy = landmarks[7,0],landmarks[7,1]
            ex, ey = landmarks[9,0],landmarks[9,1]
            angle2 = calculate_angle(dx, dy, bx, by, ex, ey)

            if line1 < line2 - 40 or line1 > line2 + 40:
                return "none"

            result = ""
            if line1 > line2 and line1 > line3:
                result += "1"
            elif line2 > line1 and line2 > line3:
                result += "2"
            else:
                result += "3"

            if line4 > line2 + 30:
                result += "1"
            else:
                result += "2"

            if line1 < line3 + 10 and line1 > line3 - 10:
                result += "1"
            elif line1 > line3 + 10:
                result += "2"
            else:
                result += "3"

            if angle <= 130:
                result += "1"
            else:
                if angle2 > 170:
                    result += "2"
                else:
                    result += "3"

            rectangular = [1111, 1112, 1113, 1121, 1122, 1123, 1211, 2111, 2112, 2113, 2121, 2122, 2123, 2131, 2132, 2133, 3111, 3112, 3113, 3131, 3132, 3133, 3211]
            round = [2213, 2223]
            square = [1212, 1213, 1223, 2212, 2231, 2232, 2233, 3212, 3213, 3231, 3232, 3233]
            oval = [2211, 2221, 2222]
            heart = [1221, 1222]

            print(result)
            for compare in rectangular:
                if int(result) == compare:
                    return "rectangular"
            for compare in round:
                if int(result) == compare:
                    return "round"
            for compare in square:
                if int(result) == compare:
                    return "square"
            for compare in oval:
                if int(result) == compare:
                    return "oval"
            for compare in heart:
                if int(result) == compare:
                    return "heart"
        return 'none'
    return 'none'

In [4]:
#importing the libraries
import numpy as np #for mathematical calculations
import cv2 #for face detection and other image operations
import dlib #for detection of facial landmarks ex:nose,jawline,eyes
from sklearn.cluster import KMeans #for clustering

import mysql.connector
#from mysql.connector import errorcode

config = {
    'host':'127.0.0.1',
    'user':'root',
    'password':'12345789',
    'database':'searchair'
}

# Construct connection string
try:
    conn = mysql.connector.connect(**config)
    print("Connection established")
except mysql.connector.Error as err:
    if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
        print("Something is wrong with the user name or password")
    elif err.errno == errorcode.ER_BAD_DB_ERROR:
        print("Database does not exist")
    else:
        print(err)
else:
    cursor = conn.cursor()
    cursor.execute("SELECT `picture`, `id` FROM `stylist_works` LIMIT 15650, 100000")
    #cursor.execute("SELECT `picture`, `id` FROM `stylist_works`")
    myresult = cursor.fetchall()     # fetchall() 获取所有记录
    
    i = 0
    for x in myresult:
        print(x)
        face_shape = get_face_shape(x[0])
        #face_shape = "none"
        print("face_shape = ", face_shape, ", str(x[1]) = ", str(x[1]))
        sql = "UPDATE stylist_works SET face_shape = '" + face_shape + "' WHERE id = " + str(x[1])
        print(sql)
        cursor.execute(sql)
        conn.commit()

Connection established
('https://cdn.style-map.com/post/photo/normal/471531.jpg', 231708)
img_src:
https://cdn.style-map.com/post/photo/normal/471531.jpg
found 1 faces!
left:  [60, 19]
right:  [90, 19]
35.714285714285715 175.0 153.57142857142858 200
0 =  -123.23171106797936 , 1 =  5.194428907734806 , angle =  128.42613997571416
0 =  -137.29061004263855 , 1 =  14.036243467926477 , angle =  151.32685351056503
face_shape =  none , str(x[1]) =  231708
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231708
('https://cdn.style-map.com/post/photo/normal/471538.jpg', 231710)
img_src:
https://cdn.style-map.com/post/photo/normal/471538.jpg
found 1 faces!
left:  [47, 15]
right:  [75, 15]
40.28776978417266 158.27338129496403 139.568345323741 200
0 =  -135.0 , 1 =  -9.782407031807287 , angle =  125.21759296819272
0 =  -150.94539590092288 , 1 =  0.0 , angle =  150.94539590092288
face_shape =  none , str(x[1]) =  231710
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231710
('https://

found 1 faces!
left:  [46, 37]
right:  [232, 37]
119.23076923076924 154.4871794871795 142.30769230769232 200
0 =  -170.98067756861835 , 1 =  -37.3493490446406 , angle =  133.63132852397774
0 =  -178.02506598911802 , 1 =  -21.370622269343187 , angle =  156.65444371977483
2133
face_shape =  rectangular , str(x[1]) =  231781
UPDATE stylist_works SET face_shape = 'rectangular' WHERE id = 231781
('https://cdn.style-map.com/post/photo/normal/471688.jpg', 231784)
img_src:
https://cdn.style-map.com/post/photo/normal/471688.jpg
found 1 faces!
left:  [24, 21]
right:  [130, 21]
126.94610778443112 165.26946107784428 150.89820359281435 200
0 =  172.23483398157467 , 1 =  -59.03624346792648 , angle =  128.72892255049885
0 =  161.56505117707798 , 1 =  -45.0 , angle =  153.43494882292202
2131
face_shape =  rectangular , str(x[1]) =  231784
UPDATE stylist_works SET face_shape = 'rectangular' WHERE id = 231784
('https://cdn.style-map.com/post/photo/normal/471689.jpg', 231785)
img_src:
https://cdn.style-m

found 1 faces!
left:  [41, 24]
right:  [115, 24]
71.15384615384616 161.53846153846155 141.34615384615384 200
0 =  -157.01128319791937 , 1 =  -20.224859431168078 , angle =  136.78642376675128
0 =  -169.9920201985587 , 1 =  -11.309932474020213 , angle =  158.6820877245385
face_shape =  none , str(x[1]) =  231846
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231846
('https://cdn.style-map.com/post/photo/normal/471837.jpg', 231847)
img_src:
https://cdn.style-map.com/post/photo/normal/471837.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  231847
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231847
('https://cdn.style-map.com/post/photo/normal/471839.jpg', 231848)
img_src:
https://cdn.style-map.com/post/photo/normal/471839.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  231848
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231848
('https://cdn.style-map.com/post/photo/normal/471849.jpg', 231854)
img_src:
https://cdn.style-map.com/post/photo/normal/47184

found 0 faces!
face_shape =  none , str(x[1]) =  231912
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231912
('https://cdn.style-map.com/post/photo/normal/471966.jpg', 231913)
img_src:
https://cdn.style-map.com/post/photo/normal/471966.jpg
found 1 faces!
left:  [35, 26]
right:  [157, 26]
103.38983050847457 149.15254237288136 133.0508474576271 200
0 =  -136.97493401088198 , 1 =  -16.82140989004083 , angle =  120.15352412084115
0 =  -154.79887635452494 , 1 =  -5.440332031005506 , angle =  149.35854432351942
face_shape =  none , str(x[1]) =  231913
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231913
('https://cdn.style-map.com/post/photo/normal/471970.jpg', 231915)
img_src:
https://cdn.style-map.com/post/photo/normal/471970.jpg
found 1 faces!
left:  [45, 15]
right:  [92, 15]
77.68595041322314 158.67768595041323 143.80165289256198 200
0 =  -157.16634582208246 , 1 =  -11.768288932020644 , angle =  145.3980568900618
0 =  -168.6900675259798 , 1 =  -4.763641690726178 , ang

found 1 faces!
left:  [10, 13]
right:  [109, 13]
188.57142857142856 161.9047619047619 140.95238095238093 200
0 =  -154.79887635452494 , 1 =  -27.89727103094763 , angle =  126.90160532357731
0 =  -173.6598082540901 , 1 =  -12.528807709151511 , angle =  161.1310005449386
1121
face_shape =  rectangular , str(x[1]) =  231955
UPDATE stylist_works SET face_shape = 'rectangular' WHERE id = 231955
('https://cdn.style-map.com/post/photo/normal/472044.jpg', 231956)
img_src:
https://cdn.style-map.com/post/photo/normal/472044.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  231956
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231956
('https://cdn.style-map.com/post/photo/normal/472048.jpg', 231958)
img_src:
https://cdn.style-map.com/post/photo/normal/472048.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  231958
UPDATE stylist_works SET face_shape = 'none' WHERE id = 231958
('https://cdn.style-map.com/post/photo/normal/472052.jpg', 231961)
img_src:
https://cdn.style-map.com/post/

...

found 0 faces!
face_shape =  none , str(x[1]) =  246131
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246131
('https://cdn.style-map.com/post/photo/normal/500620.jpg', 246132)
img_src:
https://cdn.style-map.com/post/photo/normal/500620.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246132
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246132
('https://cdn.style-map.com/post/photo/normal/500626.jpg', 246135)
img_src:
https://cdn.style-map.com/post/photo/normal/500626.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246135
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246135
('https://cdn.style-map.com/post/photo/normal/500629.jpg', 246136)
img_src:
https://cdn.style-map.com/post/photo/normal/500629.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246136
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246136
('https://cdn.style-map.com/post/photo/normal/500633.jpg', 246137)
img_src:
https://cdn.style-map.com/post/photo/normal/500633.jpg


('https://cdn.style-map.com/post/photo/normal/500736.jpg', 246183)
img_src:
https://cdn.style-map.com/post/photo/normal/500736.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246183
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246183
('https://cdn.style-map.com/post/photo/normal/500737.jpg', 246184)
img_src:
https://cdn.style-map.com/post/photo/normal/500737.jpg
found 1 faces!
left:  [0, 14]
right:  [115, 14]
196.58119658119656 174.35897435897436 162.39316239316238 200
0 =  -176.42366562500266 , 1 =  -30.06858282186245 , angle =  146.3550828031402
0 =  176.18592516570965 , 1 =  -14.036243467926477 , angle =  169.77783136636387
1223
face_shape =  square , str(x[1]) =  246184
UPDATE stylist_works SET face_shape = 'square' WHERE id = 246184
('https://cdn.style-map.com/post/photo/normal/500738.jpg', 246185)
img_src:
https://cdn.style-map.com/post/photo/normal/500738.jpg
found 1 faces!
left:  [53, 27]
right:  [163, 27]
99.5475113122172 170.13574660633483 145.70135746606334 2

found 2 faces!
face_shape =  none , str(x[1]) =  246220
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246220
('https://cdn.style-map.com/post/photo/normal/500819.jpg', 246223)
img_src:
https://cdn.style-map.com/post/photo/normal/500819.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246223
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246223
('https://cdn.style-map.com/post/photo/normal/500823.jpg', 246225)
img_src:
https://cdn.style-map.com/post/photo/normal/500823.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246225
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246225
('https://cdn.style-map.com/post/photo/normal/500826.jpg', 246226)
img_src:
https://cdn.style-map.com/post/photo/normal/500826.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246226
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246226
('https://cdn.style-map.com/post/photo/normal/500830.jpg', 246227)
img_src:
https://cdn.style-map.com/post/photo/normal/500830.jpg


face_shape =  none , str(x[1]) =  246258
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246258
('https://cdn.style-map.com/post/photo/normal/500883.jpg', 246259)
img_src:
https://cdn.style-map.com/post/photo/normal/500883.jpg
found 1 faces!
left:  [8, 24]
right:  [124, 24]
120.20725388601035 158.54922279792746 139.8963730569948 200
0 =  -143.8418145601917 , 1 =  -12.994616791916505 , angle =  130.84719776827518
0 =  -162.6459753637387 , 1 =  0.0 , angle =  162.6459753637387
2133
face_shape =  rectangular , str(x[1]) =  246259
UPDATE stylist_works SET face_shape = 'rectangular' WHERE id = 246259
('https://cdn.style-map.com/post/photo/normal/500886.jpg', 246260)
img_src:
https://cdn.style-map.com/post/photo/normal/500886.jpg
found 2 faces!
face_shape =  none , str(x[1]) =  246260
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246260
('https://cdn.style-map.com/post/photo/normal/500892.jpg', 246261)
img_src:
https://cdn.style-map.com/post/photo/normal/500892.jpg
found 1 

found 1 faces!
left:  [22, 19]
right:  [108, 19]
102.9940119760479 144.91017964071855 131.73652694610777 200
0 =  -166.4295656148385 , 1 =  -33.690067525979785 , angle =  132.73949808885874
0 =  180.0 , 1 =  -21.80140948635181 , angle =  158.19859051364818
face_shape =  none , str(x[1]) =  246290
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246290
('https://cdn.style-map.com/post/photo/normal/500970.jpg', 246292)
img_src:
https://cdn.style-map.com/post/photo/normal/500970.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246292
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246292
('https://cdn.style-map.com/post/photo/normal/500978.jpg', 246293)
img_src:
https://cdn.style-map.com/post/photo/normal/500978.jpg
found 0 faces!
face_shape =  none , str(x[1]) =  246293
UPDATE stylist_works SET face_shape = 'none' WHERE id = 246293
('https://cdn.style-map.com/post/photo/normal/500977.jpg', 246294)
img_src:
https://cdn.style-map.com/post/photo/normal/500977.jpg
found 0 

In [5]:
#importing the libraries
import numpy as np #for mathematical calculations
import cv2 #for face detection and other image operations
import dlib #for detection of facial landmarks ex:nose,jawline,eyes
from sklearn.cluster import KMeans #for clustering

import mysql.connector
#from mysql.connector import errorcode

config = {
    'host':'127.0.0.1',
    'user':'root',
    'password':'12345789',
    'database':'searchair'
}

# Construct connection string
try:
    conn = mysql.connector.connect(**config)
    print("Connection established")
except mysql.connector.Error as err:
    if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
        print("Something is wrong with the user name or password")
    elif err.errno == errorcode.ER_BAD_DB_ERROR:
        print("Database does not exist")
    else:
        print(err)
else:
    cursor = conn.cursor()
    #cursor.execute("SELECT `picture`, `id` FROM `stylist_works` LIMIT 1, 1")
    cursor.execute("SELECT `picture`, `id`, `face_shape` FROM `stylist_works`")
    myresult = cursor.fetchall()     # fetchall() 获取所有记录
    
    i = 0
    for x in myresult:
        print(x)
        print("str(x[1]) = ", str(x[0]))

Connection established
('https://cdn.style-map.com/post/photo/normal/1505.jpg', 966, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/1505.jpg
('https://cdn.style-map.com/post/photo/normal/1855.jpg', 1128, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/1855.jpg
('https://cdn.style-map.com/post/photo/normal/1858.jpg', 1129, 'square')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/1858.jpg
('https://cdn.style-map.com/post/photo/normal/1860.jpg', 1130, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/1860.jpg
('https://cdn.style-map.com/post/photo/normal/2103.jpg', 1255, 'round')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/2103.jpg
('https://cdn.style-map.com/post/photo/normal/2163.jpg', 1277, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/2163.jpg
('https://cdn.style-map.com/post/photo/normal/2180.jpg', 1284, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/2180.jpg
('https://cdn.st

str(x[1]) =  https://cdn.style-map.com/post/photo/normal/129033.jpg
('https://cdn.style-map.com/post/photo/normal/129042.jpg', 59477, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/129042.jpg
('https://cdn.style-map.com/post/photo/normal/129179.jpg', 59547, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/129179.jpg
('https://cdn.style-map.com/post/photo/normal/129296.jpg', 59599, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/129296.jpg
('https://cdn.style-map.com/post/photo/normal/129333.jpg', 59616, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/129333.jpg
('https://cdn.style-map.com/post/photo/normal/129519.jpg', 59696, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/129519.jpg
('https://cdn.style-map.com/post/photo/normal/129528.jpg', 59701, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/129528.jpg
('https://cdn.style-map.com/post/photo/normal/129575.jpg', 59723, 'none')
str(x[

('https://cdn.style-map.com/post/photo/normal/209458.jpg', 98460, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/209458.jpg
('https://cdn.style-map.com/post/photo/normal/209551.jpg', 98502, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/209551.jpg
('https://cdn.style-map.com/post/photo/normal/209623.jpg', 98535, 'square')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/209623.jpg
('https://cdn.style-map.com/post/photo/normal/211247.jpg', 98573, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/211247.jpg
('https://cdn.style-map.com/post/photo/normal/211249.jpg', 98575, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/211249.jpg
('https://cdn.style-map.com/post/photo/normal/211248.jpg', 98582, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/211248.jpg
('https://cdn.style-map.com/post/photo/normal/209749.jpg', 98610, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/209749.jpg
('ht

('https://cdn.style-map.com/post/photo/normal/279189.jpg', 133237, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/279189.jpg
('https://cdn.style-map.com/post/photo/normal/279232.jpg', 133264, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/279232.jpg
('https://cdn.style-map.com/post/photo/normal/279240.jpg', 133268, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/279240.jpg
('https://cdn.style-map.com/post/photo/normal/279268.jpg', 133286, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/279268.jpg
('https://cdn.style-map.com/post/photo/normal/279312.jpg', 133308, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/279312.jpg
('https://cdn.style-map.com/post/photo/normal/279383.jpg', 133351, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/279383.jpg
('https://cdn.style-map.com/post/photo/normal/279527.jpg', 133425, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/279527.jpg

('https://cdn.style-map.com/post/photo/normal/330626.jpg', 160867, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/330626.jpg
('https://cdn.style-map.com/post/photo/normal/330633.jpg', 160873, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/330633.jpg
('https://cdn.style-map.com/post/photo/normal/330636.jpg', 160874, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/330636.jpg
('https://cdn.style-map.com/post/photo/normal/330640.jpg', 160877, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/330640.jpg
('https://cdn.style-map.com/post/photo/normal/337447.jpg', 160883, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/337447.jpg
('https://cdn.style-map.com/post/photo/normal/330650.jpg', 160884, 'square')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/330650.jpg
('https://cdn.style-map.com/post/photo/normal/330690.jpg', 160905, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/330690.j

...

('https://cdn.style-map.com/post/photo/normal/454282.jpg', 223430, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/454282.jpg
('https://cdn.style-map.com/post/photo/normal/454283.jpg', 223431, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/454283.jpg
('https://cdn.style-map.com/post/photo/normal/454287.jpg', 223433, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/454287.jpg
('https://cdn.style-map.com/post/photo/normal/455900.jpg', 223437, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/455900.jpg
('https://cdn.style-map.com/post/photo/normal/454300.jpg', 223441, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/454300.jpg
('https://cdn.style-map.com/post/photo/normal/454301.jpg', 223442, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/454301.jpg
('https://cdn.style-map.com/post/photo/normal/454303.jpg', 223443, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/454303.jpg

str(x[1]) =  https://cdn.style-map.com/post/photo/normal/467033.jpg
('https://cdn.style-map.com/post/photo/normal/467063.jpg', 229474, 'square')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/467063.jpg
('https://cdn.style-map.com/post/photo/normal/467075.jpg', 229476, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/467075.jpg
('https://cdn.style-map.com/post/photo/normal/467093.jpg', 229483, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/467093.jpg
('https://cdn.style-map.com/post/photo/normal/467099.jpg', 229487, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/467099.jpg
('https://cdn.style-map.com/post/photo/normal/467104.jpg', 229489, 'round')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/467104.jpg
('https://cdn.style-map.com/post/photo/normal/467108.jpg', 229491, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/467108.jpg
('https://cdn.style-map.com/post/photo/normal/467110.jpg', 229492, 'non

str(x[1]) =  https://cdn.style-map.com/post/photo/normal/478080.jpg
('https://cdn.style-map.com/post/photo/normal/478082.jpg', 234915, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/478082.jpg
('https://cdn.style-map.com/post/photo/normal/478092.jpg', 234921, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/478092.jpg
('https://cdn.style-map.com/post/photo/normal/478106.jpg', 234927, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/478106.jpg
('https://cdn.style-map.com/post/photo/normal/478118.jpg', 234934, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/478118.jpg
('https://cdn.style-map.com/post/photo/normal/478142.jpg', 234950, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/478142.jpg
('https://cdn.style-map.com/post/photo/normal/478148.jpg', 234956, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/478148.jpg
('https://cdn.style-map.com/post/photo/normal/478155.jpg', 234961, 'none')

('https://cdn.style-map.com/post/photo/normal/485421.jpg', 238622, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/485421.jpg
('https://cdn.style-map.com/post/photo/normal/485422.jpg', 238623, 'square')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/485422.jpg
('https://cdn.style-map.com/post/photo/normal/485423.jpg', 238624, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/485423.jpg
('https://cdn.style-map.com/post/photo/normal/485426.jpg', 238625, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/485426.jpg
('https://cdn.style-map.com/post/photo/normal/485432.jpg', 238627, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/485432.jpg
('https://cdn.style-map.com/post/photo/normal/485438.jpg', 238629, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/485438.jpg
('https://cdn.style-map.com/post/photo/normal/485441.jpg', 238630, 'none')
str(x[1]) =  https://cdn.style-map.com/post/photo/normal/485441.j

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

